# Предсказание с помощью банковской модели

Из изменений: 

1) увеличим число повторений (решение работает очень быстро, а не использовать имеющиеся время не оптимально)

2) т.к. изменяется только 10 транзакций из 300, то можно повысить долю для сэмпла с 0.9 до 0.95

In [1]:
from submission.model import reliable_predict

In [2]:
source_file = "./data/transactions_finetune.csv"
output_path = "./data/predict.csv"
bins_path = "./submission/nn_bins.pickle"
model_path = "./submission/nn_weights.ckpt"
result = reliable_predict(source_file, bins_path, model_path)
print(result)
result.to_csv(output_path, index=False)

      user_id    target
0          69  0.017742
1         140  0.169409
2         196  0.046659
3         400  0.026146
4         544  0.076843
...       ...       ...
7075   868342  0.057727
7076   868348  0.059169
7077   868626  0.230278
7078   868878  0.009070
7079   868949  0.156628

[7080 rows x 2 columns]


# Решение

In [3]:
from catboost import CatBoostClassifier, Pool, cv
import pandas as pd

## Загрузка данных

In [4]:
targets = pd.read_csv("./data/target_finetune.csv").set_index("user_id").target
targets

user_id
452772    0
64288     0
504497    0
566270    0
328558    0
         ..
237771    0
347012    0
358770    0
292937    0
14856     0
Name: target, Length: 7080, dtype: int64

In [5]:
predict = pd.read_csv("./data/predict.csv").set_index("user_id").target.rename("nn_predict")
predict

user_id
69        0.017742
140       0.169409
196       0.046659
400       0.026146
544       0.076843
            ...   
868342    0.057727
868348    0.059169
868626    0.230278
868878    0.009070
868949    0.156628
Name: nn_predict, Length: 7080, dtype: float64

In [6]:
transactions = pd.read_csv("./data/transactions_finetune.csv", parse_dates=['transaction_dttm'])
transactions['time'] = transactions.transaction_dttm.apply(lambda x: x.hour * 3600 + x.minute * 60 + x.second)
transactions

user_id  mcc_code  currency_rk  transaction_amt    transaction_dttm  \
0             69      5541           48       -342.89792 2021-03-05 02:52:36   
1             69      5533           48      -1251.88120 2021-03-05 09:43:28   
2             69      5331           48        -87.30924 2021-03-05 11:17:23   
3             69      5921           48      -1822.17700 2021-03-05 13:41:03   
4             69      5311           48       -427.12363 2021-03-05 19:14:23   
...          ...       ...          ...              ...                 ...   
2123995   868949      5411           48       -203.11295 2021-05-11 17:05:09   
2123996   868949      4131           48        -63.25255 2021-05-13 11:28:52   
2123997   868949      4131           48        -40.04709 2021-05-13 11:38:42   
2123998   868949      4131           48       -594.77850 2021-05-13 14:00:44   
2123999   868949      5814           48       -127.33617 2021-05-13 14:17:28   

          time  
0        10356  
1        35008  
2        40643  
3        49263  
4        69263  
...        ...  
2123995  61509  
2123996  41332  
2123997  41922  
2123998  50444  
2123999  51448  

[2124000 rows x 6 columns]

## Точность банковской модели

Интересно, что reliable_predict получает выше скор на данных для дообучения, чем просто predict. Получается, что мы не только уменьшили уязвимость nn модели, но и повысили качество за счет ансамбля с **разными** сидами.

In [7]:
from sklearn.metrics import roc_auc_score

roc_auc_score(
    targets.sort_index(), 
    predict.sort_index()
)

0.683931622400516

## Создание датасета для обучения модели

Сделаем дополнительные признаки. Для клиента банка по каждому mcc коду считаем количество транзакций. Т.к. при атаке поменяется не более 10 mcc кодов, то реальное значение может изменится на ±10. Чтобы уменьшить влияние такого искажения, поделим **нацело** все значения на 20. Дополнительно добавим агрегационные признаки на основе времени в секундах.

In [8]:
mcc_code_features = transactions.pivot_table(
    index='user_id', columns=['mcc_code'], values=['transaction_amt'], 
    aggfunc=['count'], fill_value=0
)
mcc_code_features.columns = [f'{i[0]}-mcc_code:{i[2]}' for i in mcc_code_features.columns]
for col in mcc_code_features.columns:
    mcc_code_features[col] //= 20
mcc_code_features.head()

count-mcc_code:-1  count-mcc_code:742  count-mcc_code:763  \
user_id                                                              
69                       0                   0                   0   
140                      0                   0                   0   
196                      0                   0                   0   
400                      0                   0                   0   
544                      0                   0                   0   

         count-mcc_code:780  count-mcc_code:1520  count-mcc_code:1711  \
user_id                                                                 
69                        0                    0                    0   
140                       0                    0                    0   
196                       0                    0                    0   
400                       0                    0                    0   
544                       0                    0                    0   

         count-mcc_code:1731  count-mcc_code:1740  count-mcc_code:1750  \
user_id                                                                  
69                         0                    0                    0   
140                        0                    0                    0   
196                        0                    0                    0   
400                        0                    0                    0   
544                        0                    0                    0   

         count-mcc_code:1761  ...  count-mcc_code:8699  count-mcc_code:8734  \
user_id                       ...                                             
69                         0  ...                    0                    0   
140                        0  ...                    0                    0   
196                        0  ...                    0                    0   
400                        0  ...                    0                    0   
544                        0  ...                    0                    0   

         count-mcc_code:8911  count-mcc_code:8931  count-mcc_code:8999  \
user_id                                                                  
69                         0                    0                    0   
140                        0                    0                    0   
196                        0                    0                    0   
400                        0                    0                    0   
544                        0                    0                    0   

         count-mcc_code:9211  count-mcc_code:9222  count-mcc_code:9311  \
user_id                                                                  
69                         0                    0                    0   
140                        0                    0                    0   
196                        0                    0                    0   
400                        0                    0                    0   
544                        0                    0                    0   

         count-mcc_code:9399  count-mcc_code:9402  
user_id                                            
69                         0                    0  
140                        0                    0  
196                        0                    0  
400                        0                    0  
544                        0                    0  

[5 rows x 309 columns]

In [9]:
time_features = transactions.groupby('user_id')['time'].agg(['mean', 'std', 'min', 'max', 'median'])
time_features.columns = [f'tr_time_{c}' for c in time_features.columns]
time_features

tr_time_mean   tr_time_std  tr_time_min  tr_time_max  tr_time_median
user_id                                                                      
69       44718.803333  13897.253737          998        80434         46398.5
140      48630.600000  15202.399218        11227        73925         53872.0
196      39648.593333  17220.958005         2880        79221         41955.0
400      40563.100000  14845.912186         9367        82819         38959.0
544      40247.776667  21812.734081          263        86281         37744.5
...               ...           ...          ...          ...             ...
868342   50439.886667  15835.336596         1145        85685         52896.0
868348   31949.250000  18463.500917          178        85845         34700.5
868626   40233.810000  19496.431263          660        85560         40324.0
868878   47663.706667  11697.680269        26534        84771         46648.5
868949   41611.456667  19873.824711         1674        86391         40863.5

[7080 rows x 5 columns]

Т.к. банковская модель не видела данные, на которых мы будем обучать бустинг (**это важно**), то можно использовать её предсказание, как признак. 

In [10]:
df_train = pd.concat([
    predict,
    time_features,
    mcc_code_features
], axis=1)
df_train.head()

nn_predict  tr_time_mean   tr_time_std  tr_time_min  tr_time_max  \
user_id                                                                     
69         0.017742  44718.803333  13897.253737          998        80434   
140        0.169409  48630.600000  15202.399218        11227        73925   
196        0.046659  39648.593333  17220.958005         2880        79221   
400        0.026146  40563.100000  14845.912186         9367        82819   
544        0.076843  40247.776667  21812.734081          263        86281   

         tr_time_median  count-mcc_code:-1  count-mcc_code:742  \
user_id                                                          
69              46398.5                  0                   0   
140             53872.0                  0                   0   
196             41955.0                  0                   0   
400             38959.0                  0                   0   
544             37744.5                  0                   0   

         count-mcc_code:763  count-mcc_code:780  ...  count-mcc_code:8699  \
user_id                                          ...                        
69                        0                   0  ...                    0   
140                       0                   0  ...                    0   
196                       0                   0  ...                    0   
400                       0                   0  ...                    0   
544                       0                   0  ...                    0   

         count-mcc_code:8734  count-mcc_code:8911  count-mcc_code:8931  \
user_id                                                                  
69                         0                    0                    0   
140                        0                    0                    0   
196                        0                    0                    0   
400                        0                    0                    0   
544                        0                    0                    0   

         count-mcc_code:8999  count-mcc_code:9211  count-mcc_code:9222  \
user_id                                                                  
69                         0                    0                    0   
140                        0                    0                    0   
196                        0                    0                    0   
400                        0                    0                    0   
544                        0                    0                    0   

         count-mcc_code:9311  count-mcc_code:9399  count-mcc_code:9402  
user_id                                                                 
69                         0                    0                    0  
140                        0                    0                    0  
196                        0                    0                    0  
400                        0                    0                    0  
544                        0                    0                    0  

[5 rows x 315 columns]

## Обучение модели

In [11]:
train_pool = Pool(
    data=df_train,
    label=targets[df_train.index]
)

params = {
    'loss_function': 'CrossEntropy', # есть дизбаланс классов, поэтому используем CrossEntropy
    'custom_metric': ['AUC'],
    'task_type': 'CPU',
    'random_seed': 56,
    'iterations': 750,
    'max_depth': 3,
    'learning_rate': 0.01,
    'colsample_bylevel': 0.9, # помогает при малом количестве объектов
    'feature_weights': {'nn_predict': 0.9} # для защиты уменьшим важность nn модели
}

# кросс-валидация с 10 фолдами
cv_data = cv(
    params=params,
    pool=train_pool,
    fold_count=10,
    shuffle=True,
    partition_random_seed=0,
    plot=True,
    stratified=True,
    verbose=False
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [12]:
best_iter = cv_data['test-AUC-mean'].argmax()
print(f"Best iteration: {best_iter}\nBest AUC: {round(cv_data.iloc[best_iter]['test-AUC-mean'], 4)}")

Best iteration: 745
Best AUC: 0.6804


In [13]:
model_cb = CatBoostClassifier(**params)
model_cb.fit(train_pool, plot=True, verbose=False)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [14]:
# наиболее важные признаки
model_cb.get_feature_importance(prettified=True).head(10)

Feature Id  Importances
0           nn_predict    43.784605
1          tr_time_std    11.847921
2  count-mcc_code:6012     9.637959
3          tr_time_max     6.567692
4          tr_time_min     4.349295
5         tr_time_mean     3.593514
6       tr_time_median     2.643810
7  count-mcc_code:5411     2.360808
8  count-mcc_code:4829     2.163495
9  count-mcc_code:5812     1.391974

In [15]:
# сохранение весов
model_cb.save_model("./submission/model_cb.cbm")